In [1]:
import pystac_client
import folium
from odc import stac as odc_stac
import xarray as xr
import numpy as np
import datetime

## EODC catalog

In [2]:
eodc_catalog = pystac_client.Client.open("https://stac.eodc.eu/api/v1")
eodc_catalog

<Client id=stac-fastapi>

## Cube definitions

In [3]:
crs = "EPSG:4326" # Coordinate Reference System - World Geodetic System 1984 (WGS84) in this case 
res = 0.00018 # 20 meter in degree

## Northern Gemany Flood

Storm Babet hit the Denmark and Northern coast at the 20th of October 2023 [Wikipedia](https://en.wikipedia.org/wiki/Storm_Babet).


In [4]:
time_range = "2022-10-15/2022-10-22"
minlon, maxlon = 12.3, 12.9
minlat, maxlat = 54.4, 54.6
bounding_box = [minlon, minlat, maxlon, maxlat]

## Microwave backscatter measurements

In [5]:
collection_sig0 = "SENTINEL1_SIG0_20M"
collection = eodc_catalog.get_collection(collection_sig0)
collection

<CollectionClient id=SENTINEL1_SIG0_20M>

In [6]:
search = eodc_catalog.search(
    collections=collection_sig0,
    bbox=bounding_box,
    datetime=time_range,
)

items_sig0 = search.item_collection()
print(f"On EODC we found {len(items_sig0)} items for the given search query")
items_sig0

On EODC we found 27 items for the given search query


In [7]:
scale = items_sig0[0].assets['VV'].extra_fields.get('raster:bands')[0]['scale'] # raster:bands is STAC raster extension
nodata = items_sig0[0].assets['VV'].extra_fields.get('raster:bands')[0]['nodata']

In [14]:
bands = "VV"
sig0_dc = odc_stac.load(items_sig0,
                        bands=bands,
                        crs=crs,
                        chunks={'time':5},
                        resolution=res,
                        bbox=bounding_box,
                        )
sig0_dc = sig0_dc.where(sig0_dc != nodata) / scale
sig0_dc

<xarray.Dataset> Size: 311MB
Dimensions:      (latitude: 1112, longitude: 3334, time: 21)
Coordinates:
  * latitude     (latitude) float64 9kB 54.6 54.6 54.6 54.6 ... 54.4 54.4 54.4
  * longitude    (longitude) float64 27kB 12.3 12.3 12.3 12.3 ... 12.9 12.9 12.9
    spatial_ref  int32 4B 4326
  * time         (time) datetime64[ns] 168B 2022-10-16T05:33:14 ... 2022-10-2...
Data variables:
    VV           (time, latitude, longitude) float32 311MB dask.array<chunksize=(5, 1112, 3334), meta=np.ndarray>

## Harmonic parameters

In [10]:
collection_hpar = "SENTINEL1_HPAR"
collection = eodc_catalog.get_collection(collection_hpar)
collection

<CollectionClient id=SENTINEL1_HPAR>

In [11]:
search = eodc_catalog.search(
    collections=collection_hpar,
    bbox=bounding_box
)

items_hpar = search.item_collection()
print(f"On EODC we found {len(items_hpar)} items for the given search query")
items_hpar

On EODC we found 19 items for the given search query


In [12]:
scale = items_hpar[0].assets['C1'].extra_fields.get('raster:bands')[0]['scale'] # raster:bands is STAC raster extension
nodata = items_hpar[0].assets['C1'].extra_fields.get('raster:bands')[0]['nodata']

In [13]:
bands = ("C1", "C2", "C3", "M0", "S1", "S2", "S3", "STD", "NOBS")
hpar_dc = odc_stac.load(items_hpar,
                        bands=bands,
                        crs=crs,
                        resolution=res,
                        bbox=bounding_box,
                        ).\
    rename_vars({"NOBS": "NOBS_HPAR"}).\
    squeeze("time").\
    drop_vars("time")
hpar_dc = hpar_dc.where(hpar_dc != nodata) / scale
hpar_dc

<xarray.Dataset> Size: 134MB
Dimensions:      (latitude: 1112, longitude: 3334)
Coordinates:
  * latitude     (latitude) float64 9kB 54.6 54.6 54.6 54.6 ... 54.4 54.4 54.4
  * longitude    (longitude) float64 27kB 12.3 12.3 12.3 12.3 ... 12.9 12.9 12.9
    spatial_ref  int32 4B 4326
Data variables:
    C1           (latitude, longitude) float32 15MB 1.4 1.5 1.5 ... 0.1 0.0 0.0
    C2           (latitude, longitude) float32 15MB 0.5 0.6 0.6 ... 0.3 0.3 0.3
    C3           (latitude, longitude) float32 15MB -0.1 0.0 0.0 ... 0.0 0.0 0.0
    M0           (latitude, longitude) float32 15MB -20.0 -20.0 ... -10.4 -10.4
    S1           (latitude, longitude) float32 15MB -0.8 -0.6 -0.6 ... 0.1 0.1
    S2           (latitude, longitude) float32 15MB 0.0 0.0 0.0 ... 0.0 0.0 0.0
    S3           (latitude, longitude) float32 15MB -0.7 -0.6 -0.6 ... 0.0 0.0
    STD          (latitude, longitude) float32 15MB 4.2 4.2 4.2 ... 0.9 0.9 0.9
    NOBS_HPAR    (latitude, longitude) float32 15MB 18.0 18.0 18.0 ... 17.9 17.9

## Local Incidence Angles

In [20]:
collection_plia = "SENTINEL1_MPLIA"
collection = eodc_catalog.get_collection(collection_plia)
collection

<CollectionClient id=SENTINEL1_MPLIA>

In [21]:
search = eodc_catalog.search(
    collections=collection_plia,
    bbox=bounding_box
)

items_plia = search.item_collection()
print(f"On EODC we found {len(items_plia)} items for the given search query")
items_plia

On EODC we found 19 items for the given search query


In [22]:
scale = items_plia[0].assets["MPLIA"].extra_fields.get('raster:bands')[0]['scale'] # raster:bands is STAC raster extension
nodata = items_plia[0].assets["MPLIA"].extra_fields.get('raster:bands')[0]['nodata']

In [23]:
bands = ("MPLIA", "NOBS")
plia_dc = odc_stac.load(items_plia,
                        bands=bands,
                        crs=crs,
                        resolution=res,
                        bbox=bounding_box,
                        ).\
    rename_vars({"NOBS": "NOBS_MPLIA"}).\
    squeeze("time").\
    drop_vars("time")
plia_dc = plia_dc.where(plia_dc != nodata) / scale
plia_dc

<xarray.Dataset> Size: 30MB
Dimensions:      (latitude: 1112, longitude: 3334)
Coordinates:
  * latitude     (latitude) float64 9kB 54.6 54.6 54.6 54.6 ... 54.4 54.4 54.4
  * longitude    (longitude) float64 27kB 12.3 12.3 12.3 12.3 ... 12.9 12.9 12.9
    spatial_ref  int32 4B 4326
Data variables:
    MPLIA        (latitude, longitude) float32 15MB 43.05 43.05 ... 39.28 39.28
    NOBS_MPLIA   (latitude, longitude) float32 15MB 0.61 0.61 0.61 ... 0.61 0.61

## Fuse cube


In [24]:
flood_dc = xr.merge([sig0_dc, plia_dc, hpar_dc])

In [25]:
flood_dc

<xarray.Dataset> Size: 475MB
Dimensions:      (latitude: 1112, longitude: 3334, time: 21)
Coordinates:
  * latitude     (latitude) float64 9kB 54.6 54.6 54.6 54.6 ... 54.4 54.4 54.4
  * longitude    (longitude) float64 27kB 12.3 12.3 12.3 12.3 ... 12.9 12.9 12.9
    spatial_ref  int32 4B 4326
  * time         (time) datetime64[ns] 168B 2022-10-16T05:33:14 ... 2022-10-2...
Data variables:
    VV           (time, latitude, longitude) float32 311MB dask.array<chunksize=(5, 1112, 3334), meta=np.ndarray>
    MPLIA        (latitude, longitude) float32 15MB 43.05 43.05 ... 39.28 39.28
    NOBS_MPLIA   (latitude, longitude) float32 15MB 0.61 0.61 0.61 ... 0.61 0.61
    C1           (latitude, longitude) float32 15MB 1.4 1.5 1.5 ... 0.1 0.0 0.0
    C2           (latitude, longitude) float32 15MB 0.5 0.6 0.6 ... 0.3 0.3 0.3
    C3           (latitude, longitude) float32 15MB -0.1 0.0 0.0 ... 0.0 0.0 0.0
    M0           (latitude, longitude) float32 15MB -20.0 -20.0 ... -10.4 -10.4
    S1           (latitude, longitude) float32 15MB -0.8 -0.6 -0.6 ... 0.1 0.1
    S2           (latitude, longitude) float32 15MB 0.0 0.0 0.0 ... 0.0 0.0 0.0
    S3           (latitude, longitude) float32 15MB -0.7 -0.6 -0.6 ... 0.0 0.0
    STD          (latitude, longitude) float32 15MB 4.2 4.2 4.2 ... 0.9 0.9 0.9
    NOBS_HPAR    (latitude, longitude) float32 15MB 18.0 18.0 18.0 ... 17.9 17.9

## Likelihoods

### Water

In [18]:
def calc_water_likelihood(dc):
    return  dc.MPLIA * -0.394181 + -4.142015

flood_dc["wbsc"] = calc_water_likelihood(flood_dc)

### Land

In [16]:
def harmonic_expected_backscatter_(dc, dtime_str):
    w = np.pi * 2 / 365
    dt = datetime.datetime.strptime(dtime_str, "%Y-%m-%d")
    t = dt.timetuple().tm_yday
    wt = w * t
    
    M0 = dc.M0
    S1 = dc.S1
    S2 = dc.S2
    S3 = dc.S3
    C1 = dc.C1
    C2 = dc.C2
    C3 = dc.C3
    hm_c1 = (M0 + S1 * np.sin(wt)) + (C1 * np.cos(wt))
    hm_c2 = ((hm_c1 + S2 * np.sin(2 * wt)) + C2 * np.cos(2 * wt))
    hm_c3 = ((hm_c2 + S3 * np.sin(3 * wt)) + C3 * np.cos(3 * wt))
    return hm_c3



In [17]:
harmonic_expected_backscatter_(flood_dc, "2018-01-01")

NameError: name 'flood_dc' is not defined

## Flood mappingg

In [ ]:
def bayesian_flood_decision(water_likelihood, land_likelihood):
    evidence = (water_likelihood * 0.5) + (land_likelihood * 0.5)
    nf_post_prob = (water_likelihood * 0.5) / evidence
    f_post_prob = (land_likelihood * 0.5) / evidence
    return np.greater(f_post_prob, nf_post_prob)
flood_dc["decision"] = bayesian_flood_decision(flood_dc.wbsc, flood_dc.hbsc)
flood_dc

In [ ]:
flood_dc.decision.plot()